In [1]:
import argparse
import math
from tqdm import tqdm
from Bio.SeqIO.FastaIO import Seq, SeqRecord
import lmdb

from typing import Union, List, Tuple, Sequence, Dict, Any, Optional, Collection
from copy import copy
from pathlib import Path
import pickle as pkl
import logging
import random

import json
import lmdb
import numpy as np
import torch
import torch.nn.functional as F
from torch.utils.data import Dataset
from scipy.spatial.distance import pdist, squareform


class LMDBDataset(Dataset):
    """Creates a dataset from an lmdb file.
    Args:
        data_file (Union[str, Path]): Path to lmdb file.
        in_memory (bool, optional): Whether to load the full dataset into memory.
            Default: False.
    """

    def __init__(self,
                 data_file: Union[str, Path],
                 in_memory: bool = False):

        data_file = Path(data_file)
        if not data_file.exists():
            raise FileNotFoundError(data_file)

        env = lmdb.open(str(data_file), max_readers=1, readonly=True,
                        lock=False, readahead=False, meminit=False)

        with env.begin(write=False) as txn:
            num_examples = pkl.loads(txn.get(b'num_examples'))

        if in_memory:
            cache = [None] * num_examples
            self._cache = cache

        self._env = env
        self._in_memory = in_memory
        self._num_examples = num_examples

    def __len__(self) -> int:
        return self._num_examples

    def __getitem__(self, index: int):
        if not 0 <= index < self._num_examples:
            raise IndexError(index)

        if self._in_memory and self._cache[index] is not None:
            item = self._cache[index]
        else:
            with self._env.begin(write=False) as txn:
                item = pkl.loads(txn.get(str(index).encode()))
                if 'id' not in item:
                    item['id'] = str(index)
                if self._in_memory:
                    self._cache[index] = item
        return item


In [20]:
# parser = argparse.ArgumentParser(description='Convert an lmdb file into a fasta file')
# parser.add_argument('lmdbfile', type=str, help='The lmdb file to convert')
# parser.add_argument('fastafile', type=str, help='The fasta file to output')
# args = parser.parse_args()
# lmdbfile = args.lmdbfile
# fastafile = args.fastafile

In [44]:
def calc(item):
    # protein_length = len(item['primary'])
    token_ids = item['primary']
    input_mask = np.ones_like(token_ids)
    valid_mask = item['valid_mask']
    contact_map = np.less(squareform(pdist(item['tertiary'])), 8.0).astype(np.int64)

    yind, xind = np.indices(contact_map.shape)
    invalid_mask = ~(valid_mask[:, None] & valid_mask[None, :])
    invalid_mask |= np.abs(yind - xind) < 6
    contact_map[invalid_mask] = -1

    return contact_map, squareform(pdist(item['tertiary']))

In [65]:
def process(task, split):
    Path(f'./output/{task}').mkdir(exist_ok=True)
    lmdbfile = f'./data/{task}/{task}_{split}.lmdb'
    fastafile = f'./output/{task}/{task}_{split}'
    dataset = LMDBDataset(lmdbfile)

    if not fastafile.endswith('.fasta'):
        fastafile += '.fasta'

    data = list()
    task_specific = list()
    id_fill = math.ceil(math.log10(len(dataset)))
    for i, element in enumerate(tqdm(dataset)):
        id_ = element.get('id', str(i).zfill(id_fill))
        print(id_)
        if isinstance(id_, bytes):
            id_ = id_.decode()
    
        primary = element['primary']
        seq = Seq(primary)
        print(element)
        data.append(element)

    with open(fastafile, 'w') as f:
        for idx, i in enumerate(data):
            seq = i['primary']
            if task == 'fluorescence':
                target = float(i['log_fluorescence'][0])
            elif task == 'stability':
                target = float(i['stability_score'][0])
            elif task == 'remote_homology':
                target = i['fold_label']
            elif task == 'proteinnet':
                target, dist_mat = calc(i)
            elif task == 'secondary_structure':
                target = np.asarray(i['ss3'], np.int64)
                target = np.pad(target, (1, 1), 'constant', constant_values=-1)
            task_specific.append([seq, target])
            # f.write(f">{str(idx).zfill(id_fill)}_{target}\n{seq}\n")
            f.write(f">{str(idx).zfill(id_fill)}\n{seq}\n")
    np.save(f'./output/labels/{task}_{split}', data)
    return task_specific, data

In [66]:
data, _ = process('fluorescence', 'test')

  2%|████▊                                                                                                                                                                                                                       | 589/27217 [00:00<00:09, 2908.31it/s]

0
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDDGNYKTRDEVKFEGDTLVNRIELKGIDFKEDGNILGHKLEYNYDSHNVYIMADKQKNGIKVNFKIRHNIEDGSVQLADHYQQNTPVGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGTDEPYK', 'protein_length': 237, 'log_fluorescence': array([1.3010312], dtype=float32), 'num_mutations': 5, 'id': '0'}
1
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDDGNYKTRDEVKFEGDTLVNRIELKGIDFKEDGNILGHKLENNYNSLNVYIMADKQKNGIKVNFKIRHNIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLGFVTAAGITHGMDELYK', 'protein_length': 237, 'log_fluorescence': array([1.3011891], dtype=float32), 'num_mutations': 4, 'id': '1'}
2
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDDGNYKTRGEVKFEGDTLVNRIELKGIDFKEDGNILGHMLEYNYNSHNVYIMADKQKNGIKVNFKICHNIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDEPYK', 'protein_length':

  5%|██████████▏                                                                                                                                                                                                                | 1262/27217 [00:00<00:08, 3122.37it/s]


591
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDGGNYKTRAEVKFEGDTLVNRIELKGIDFKEDGNILGHKLEYNYNSHNVYIMADEQKNGIKVNFKIRHNIEDGSVQLADHYQQNFPIGDGPVLLPDNHYLCTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDELYK', 'protein_length': 237, 'log_fluorescence': array([3.4242625], dtype=float32), 'num_mutations': 4, 'id': '591'}
592
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDGGNYKTRAEVKFEGDTLVNRIELKGIDFKEDGNILGHKLEYNYNSHNVYIMADKQENGIKVNFKIRHNIEDGSVQLADHYQQNTPIGDGPVLLPDDHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDALYK', 'protein_length': 237, 'log_fluorescence': array([3.2611382], dtype=float32), 'num_mutations': 4, 'id': '592'}
593
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDGGNYKTRAEVKFEGDTLVNRIELKGIDFKEDGNILGHKQEYNYNSHSVYIMADKQKNGIKVNFKIRHNIGDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLPELVTAAGITHGMDELYK', 'prote

  7%|███████████████▋                                                                                                                                                                                                           | 1944/27217 [00:00<00:07, 3261.57it/s]

...

25659
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYIQERTIFFKDDGNYKTRAEVKFEGDTLVNRIELKGIDFKEDGNILGHKLEYNYNSHNVYIMADKQKNGIKVNFKIRHYIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGTTRGMDELYK', 'protein_length': 237, 'log_fluorescence': array([3.5666826], dtype=float32), 'num_mutations': 4, 'id': '25659'}
25660
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYIQEHTIFFKDDGNYMTRAEVKFEGDTLVNRIELKGIDFKEDGNILGHKLEYNYNSHNVYIVADKQKNGIKVNFKIRHNIEDGSVQLADHYQQNTPIGDGPALLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDELYK', 'protein_length': 237, 'log_fluorescence': array([1.5912938], dtype=float32), 'num_mutations': 5, 'id': '25660'}
25661
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYIQERTIFFKDDGNYKTRAEVKFEGDTLVNRIELKGIDFKEDGNILGHKLEYNNNSHNVYIMAGKQKNGIKVYFKIRHNIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDELYK

 98%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉     | 26582/27217 [00:08<00:00, 3082.48it/s]

26223
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPRPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDDGNYKTRAEVKFEGDTLVNRIELKGFGFKEDGNILGHKLEYNYNSHNVYIMADKQKDGIKVNFKIRHNIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITRGMDELYK', 'protein_length': 237, 'log_fluorescence': array([1.30103], dtype=float32), 'num_mutations': 5, 'id': '26223'}
26224
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPRPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTNFFKDDGNYKTRAEVKFEGDTLVNRIELKGIDFKEDGNILGHKLEYNYNSHNVYIMADKQKNGIKVNFKIRHNIEDGSVQLADHYQRNTPIGDGPVLLPDNQYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDELYK', 'protein_length': 237, 'log_fluorescence': array([1.7292032], dtype=float32), 'num_mutations': 4, 'id': '26224'}
26225
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPRPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTTFFKDDGNYKTRAEVKFEGDTLVNRIELEGIDFKEDGNILGHKLEYNYNSHNVYIMADKQKNGIKVNFKIRHNIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQAALSKDPNEKRDHMVLLEFATAAGITHGMDELYK',

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 27217/27217 [00:08<00:00, 3307.52it/s]


26882
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSDGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDDGNYKTRAEVEFEGDTLVNRIELKGIDFKEDGNILGHKLEYNYNNHNVYIMADKQKDGIKVNFKIRHNIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDELYK', 'protein_length': 237, 'log_fluorescence': array([1.2978274], dtype=float32), 'num_mutations': 4, 'id': '26882'}
26883
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSDGVQCFSRYPDHMKQHDFFSAMPEGYVQERTIFFKDDGNYKTRAEVKFEGDTLVNRTELKGIDFKEDGNILGHKLEYNYNSHNVYIMADKQKNGIKENFKIRHDIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDELYK', 'protein_length': 236, 'log_fluorescence': array([1.7108358], dtype=float32), 'num_mutations': 5, 'id': '26883'}
26884
{'primary': 'SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSDGVQCFSRYPDHMKQHDFFKSAMPEGYVRERTIFFKDDGNYKTRAEVKFEGDTLVNRIEPKGIDFKEDGNILGHKLEYNYNSHNVYIMADKQKNGIKVNFKIRHNIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLGTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDELYK'

In [62]:
data

[['SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDDGNYKTRDEVKFEGDTLVNRIELKGIDFKEDGNILGHKLEYNYDSHNVYIMADKQKNGIKVNFKIRHNIEDGSVQLADHYQQNTPVGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGTDEPYK',
  1.301031231880188],
 ['SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDDGNYKTRDEVKFEGDTLVNRIELKGIDFKEDGNILGHKLENNYNSLNVYIMADKQKNGIKVNFKIRHNIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLGFVTAAGITHGMDELYK',
  1.3011890649795532],
 ['SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDDGNYKTRGEVKFEGDTLVNRIELKGIDFKEDGNILGHMLEYNYNSHNVYIMADKQKNGIKVNFKICHNIEDGSVQLADHYQQNTPIGDGPVLLPDNHYLSTQSALSKDPNEKRDHMVLLEFVTAAGITHGMDEPYK',
  3.582764148712158],
 ['SKGEELFTGVVPILVELDGDVNGHKFSVSGEGEGDATYGKLTLKFICTTGKLPVPWPTLVTTLSYGVQCFSRYPDHMKQHDFFKSAMPEGYVQERTIFFKDDGNYKTRGEVKFEGDTLVNRIELKGIDFKEDGNILGHKLEYNYNSHNVYIMADEQKNGIKVNSKIRHNIEDGSVQLADHYQQNTPIGDGPVQPPDNHYLS

In [59]:
tasks = ['fluorescence', 'stability', 'proteinnet']
splits = ['train', 'valid', 'test']
for t in tasks:
    for s in splits:
        data, _ = process(t, s)
for s in ['train', 'valid', 'casp12', 'ts115', 'cb513']:
    data, _ = process('secondary_structure', s)

for s in ['train', 'valid', 'test_fold_holdout', 'test_family_holdout', 'test_superfamily_holdout']:
    data, _ = process('remote_homology', s)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 53614/53614 [00:00<00:00, 109582.41it/s]


KeyboardInterrupt: 

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 513/513 [00:00<00:00, 19416.15it/s]


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1254/1254 [00:00<00:00, 38525.51it/s]
